In [1]:
import duckdb
import altair as alt
import pandas as pd
import os
conn = duckdb.connect(':memory:')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
benchmark_data = []
for tracker in ["SORT", "DeepSORT"]:
    root = f"track-accuracy-{tracker.lower()}/xsort"
    for folder in os.listdir(root):
        video, _, _, skip, _ = folder.split("-")[1].split(".")
        # print(tracker, video, skip)
        csvfile = os.path.join(root, folder, "car_detailed.csv")
        table = conn.read_csv(csvfile).query("t", "select * EXCLUDE (seq) from t WHERE seq IS NOT NULL LIMIT 1").fetchnumpy()

        for key in table.keys():
            matrics, *thresholds = key.split("___")
            threshold = thresholds[0] if len(thresholds) > 0 else None
            value = table[key][0]
            # print(matrics, threshold, value)
            benchmark_data.append({
                "tracker": tracker,
                "video": video,
                "skip": skip,
                "matrics": matrics,
                "threshold": threshold,
                "value": value
            })

In [3]:
df = pd.DataFrame.from_records(benchmark_data)

In [4]:
df

tracker  video skip      matrics threshold         value
0          SORT  jnc02  002      HOTA(0)      None      0.986564
1          SORT  jnc02  002      LocA(0)      None      0.989651
2          SORT  jnc02  002  HOTALocA(0)      None      0.976354
3          SORT  jnc02  002         HOTA         5      0.986564
4          SORT  jnc02  002         HOTA        10      0.986564
...         ...    ...  ...          ...       ...           ...
32599  DeepSORT  jnc05  001      HOTA_FP       AUC      0.000000
32600  DeepSORT  jnc05  001         Dets      None  55880.000000
32601  DeepSORT  jnc05  001      GT_Dets      None  55880.000000
32602  DeepSORT  jnc05  001          IDs      None    132.000000
32603  DeepSORT  jnc05  001       GT_IDs      None    132.000000

[32604 rows x 6 columns]

In [11]:
alt.Chart(df).mark_line(point=True).transform_filter(filter='((datum.matrics === "HOTA" && datum.threshold === "20")) && datum.skip <= 64').encode(
    x=alt.X('skip:Q', title="Sampling Interval (frames)"),
    y=alt.Y('value:Q', title="HOTA Score"),
    color="tracker:N",
    facet=alt.Facet('video:N', columns=3),
    # row='matrics:N',
    detail="video:N"
)

alt.Chart(...)